# Backtesting with NautilusTrader

---

In this notebook, I'll experiment with a simple backtesting strategy using the **`NautilusTrader`** library. The strategy will be tested on **Bitcoin/USD 1-hour interval data**. This workflow will demonstrate how to set up, implement, and evaluate a trading strategy using historical data.

## High-level API

The high-level API centers around a **`BacktestNode`**, which orchestrates the management of multiple `BacktestEngine` instances. Each `BacktestEngine` is defined by a `BacktestRunConfig`. Multiple configurations can be bundled into a list and processed by the node in a single run.

Each **`BacktestRunConfig`** object consists of the following:

* A list of `BacktestDataConfig` objects.
* A list of `BacktestVenueConfig` objects.
* A list of `ImportableActorConfig` objects.
* A list of `ImportableStrategyConfig` objects.
* A list of `ImportableExecAlgorithmConfig` objects.
* An optional `ImportableControllerConfig` object.
* An optional `BacktestEngineConfig` object, with a default configuration if not specified.

In [1]:
import os
import sys
# Add src folder to Python path
root_path = os.path.abspath(os.path.join(os.getcwd(), ".."))
sys.path.append(root_path)

## Load data

In [2]:
import polars as pl
from src.utils.utils import polars_to_pandas
# from src.config import config

In [3]:
df = pl.read_parquet("../data/BTCUSDT_1h_tmp_365days.parquet")
df.head()

shape: (5, 12)
┌──────────────┬──────────┬──────────┬──────────┬───┬────────┬──────────────┬─────────────┬────────┐
│ open_time    ┆ open     ┆ high     ┆ low      ┆ … ┆ trades ┆ taker_base_v ┆ taker_quote ┆ ignore │
│ ---          ┆ ---      ┆ ---      ┆ ---      ┆   ┆ ---    ┆ ol           ┆ _vol        ┆ ---    │
│ datetime[ms] ┆ f64      ┆ f64      ┆ f64      ┆   ┆ i64    ┆ ---          ┆ ---         ┆ str    │
│              ┆          ┆          ┆          ┆   ┆        ┆ f64          ┆ f64         ┆        │
╞══════════════╪══════════╪══════════╪══════════╪═══╪════════╪══════════════╪═════════════╪════════╡
│ 2024-09-24   ┆ 63159.99 ┆ 63372.45 ┆ 63088.02 ┆ … ┆ 175340 ┆ 250.56544    ┆ 1.5842e7    ┆ 0      │
│ 16:00:00     ┆          ┆          ┆          ┆   ┆        ┆              ┆             ┆        │
│ 2024-09-24   ┆ 63262.01 ┆ 64000.0  ┆ 63241.75 ┆ … ┆ 264552 ┆ 766.68339    ┆ 4.8839e7    ┆ 0      │
│ 17:00:00     ┆          ┆          ┆          ┆   ┆        ┆              ┆             ┆        │
│ 2024-09-24   ┆ 63775.54 ┆ 63886.0  ┆ 63540.48 ┆ … ┆ 178871 ┆ 316.93669    ┆ 2.0201e7    ┆ 0      │
│ 18:00:00     ┆          ┆          ┆          ┆   ┆        ┆              ┆             ┆        │
│ 2024-09-24   ┆ 63727.58 ┆ 64375.0  ┆ 63682.93 ┆ … ┆ 206037 ┆ 831.68881    ┆ 5.3270e7    ┆ 0      │
│ 19:00:00     ┆          ┆          ┆          ┆   ┆        ┆              ┆             ┆        │
│ 2024-09-24   ┆ 64292.35 ┆ 64596.53 ┆ 64093.15 ┆ … ┆ 254197 ┆ 817.49704    ┆ 5.2583e7    ┆ 0      │
│ 20:00:00     ┆          ┆          ┆          ┆   ┆        ┆              ┆             ┆        │
└──────────────┴──────────┴──────────┴──────────┴───┴────────┴──────────────┴─────────────┴────────┘

### POC design — Data ingest + catalog write

In [4]:
from __future__ import annotations
import polars as pl
from pathlib import Path
from nautilus_trader.model import BarType
from nautilus_trader.persistence.catalog import ParquetDataCatalog
from nautilus_trader.persistence.wranglers import BarDataWrangler
from nautilus_trader.test_kit.providers import TestInstrumentProvider
from decimal import Decimal

In [5]:
CATALOG_PATH = Path.cwd() / "catalog"
CATALOG_PATH.mkdir(parents=True, exist_ok=True)

# Create a catalog instance
catalog = ParquetDataCatalog(CATALOG_PATH)

In [6]:
BTCUSD = TestInstrumentProvider.btcusdt_binance()
print(BTCUSD)

CurrencyPair(id=BTCUSDT.BINANCE, raw_symbol=BTCUSDT, asset_class=CRYPTOCURRENCY, instrument_class=SPOT, quote_currency=USDT, is_inverse=False, price_precision=2, price_increment=0.01, size_precision=6, size_increment=0.000001, multiplier=1, lot_size=None, margin_init=0, margin_maint=0, maker_fee=0.001, taker_fee=0.001, info=None)


OBLIGATORIO: Pandas df con timestamp como indice

In [7]:
df = df.with_columns(
        (pl.col("open_time") + pl.duration(hours=1)).alias("timestamp"),
    ).to_pandas()

# Change order of columns
df = df.reindex(columns=["timestamp", "open", "high", "low", "close", "volume"])
df = df.set_index("timestamp")
print(df.shape)
df.head()

(8760, 5)


open      high       low     close      volume
timestamp                                                              
2024-09-24 17:00:00  63159.99  63372.45  63088.02  63262.00   524.87788
2024-09-24 18:00:00  63262.01  64000.00  63241.75  63775.86  1504.89392
2024-09-24 19:00:00  63775.54  63886.00  63540.48  63727.58   804.94922
2024-09-24 20:00:00  63727.58  64375.00  63682.93  64292.34  1316.46046
2024-09-24 21:00:00  64292.35  64596.53  64093.15  64215.01  1610.30279

In [8]:
BTCUSD_SPOT_1HOUR_BARTYPE = BarType.from_str(
    f"{BTCUSD.id}-1-HOUR-LAST-EXTERNAL"
)

In [9]:
wrangler = BarDataWrangler(bar_type=BTCUSD_SPOT_1HOUR_BARTYPE, instrument=BTCUSD)
BARS = wrangler.process(df)

In [10]:
catalog.write_data([BTCUSD])

In [11]:
catalog.write_data(BARS)

In [12]:
# Read and analyze data from the catalog
# - Retrieve all instrument definitions
all_instruments = catalog.instruments()
print(f"All instruments:\n{all_instruments}")

# - Get all available bars
all_bars = catalog.bars()
print(f"All bars count: {len(all_bars)}")

All instruments:
[CurrencyPair(id=BTCUSDT.BINANCE, raw_symbol=BTCUSDT, asset_class=CRYPTOCURRENCY, instrument_class=SPOT, quote_currency=USDT, is_inverse=False, price_precision=2, price_increment=0.01, size_precision=6, size_increment=0.000001, multiplier=1, lot_size=None, margin_init=0, margin_maint=0, maker_fee=0.001, taker_fee=0.001, info=None)]
All bars count: 8760


## Simple bt - High-Level API (BacktestNode)

In [13]:
from nautilus_trader.config import BacktestEngineConfig, BacktestDataConfig, BacktestVenueConfig, BacktestRunConfig
from nautilus_trader.backtest.node import BacktestNode
from nautilus_trader.model import Bar
from nautilus_trader.model import Money, Venue
from nautilus_trader.model.enums import OmsType
from nautilus_trader.model.enums import AccountType
from nautilus_trader.config import ImportableStrategyConfig
from nautilus_trader.model.currencies import BTC
from nautilus_trader.model.currencies import USDT

Configure Data

In [14]:
data_config = BacktestDataConfig(
        catalog_path = str(CATALOG_PATH),
        data_cls=Bar,
        instrument_id=BTCUSD.id,
        bar_types=[BTCUSD_SPOT_1HOUR_BARTYPE],
    )
data_config

BacktestDataConfig(catalog_path='/Users/ezequiel.rivero/personal/tradelab_repositories/Crypto-Backtester-Duel/notebooks/catalog', data_cls=<class 'nautilus_trader.model.data.Bar'>, catalog_fs_protocol=None, catalog_fs_storage_options=None, instrument_id=InstrumentId('BTCUSDT.BINANCE'), start_time=None, end_time=None, filter_expr=None, client_id=None, metadata=None, bar_spec=None, instrument_ids=None, bar_types=[BarType(BTCUSDT.BINANCE-1-HOUR-LAST-EXTERNAL)])

Configure Venue

In [15]:
from nautilus_trader.adapters.binance import BINANCE_VENUE

# VENUE = Venue("BINANCE")

venue_config = BacktestVenueConfig(
        name=str(BINANCE_VENUE), #str(VENUE),
        oms_type="NETTING",
        account_type="CASH",  # Spot CASH account (not for perpetuals or futures)
        base_currency=None,  # Multi-currency account
        starting_balances=[Money(1_000_000.0, USDT), Money(1.0, BTC)],
    )
venue_config

BacktestVenueConfig(name='BINANCE', oms_type='NETTING', account_type='CASH', starting_balances=[Money(1000000.00000000, USDT), Money(1.00000000, BTC)], base_currency=None, default_leverage=1.0, leverages=None, margin_model=None, modules=None, fill_model=None, latency_model=None, fee_model=None, book_type='L1_MBP', routing=False, reject_stop_orders=True, support_gtd_orders=True, support_contingent_orders=True, use_position_ids=True, use_random_ids=False, use_reduce_only=True, bar_execution=True, bar_adaptive_high_low_ordering=False, trade_execution=False, allow_cash_borrowing=False, frozen_account=False)

Configure Strategy

In [16]:
strategies = [
    ImportableStrategyConfig(
        strategy_path="nautilus_trader.examples.strategies.ema_cross:EMACross",
        config_path="nautilus_trader.examples.strategies.ema_cross:EMACrossConfig",
        config={
            "instrument_id": BTCUSD.id,
            "bar_type": BTCUSD_SPOT_1HOUR_BARTYPE,
            "fast_ema_period": 30,
            "slow_ema_period": 100,
            "trade_size": Decimal("1"),
        },
    ),
    ImportableStrategyConfig(
        strategy_path="src.strategies.nautilus:SmaCrossNT",
        config_path="src.strategies.nautilus:SmaCrossConfig",
        config={
            "instrument_id": BTCUSD.id,
            "bar_type": BTCUSD_SPOT_1HOUR_BARTYPE,
            "fast_sma_period": 30,
            "slow_sma_period": 100,
            "trade_size": Decimal("1"),
        },
    ),
]
strategies

[ImportableStrategyConfig(strategy_path='nautilus_trader.examples.strategies.ema_cross:EMACross', config_path='nautilus_trader.examples.strategies.ema_cross:EMACrossConfig', config={'instrument_id': InstrumentId('BTCUSDT.BINANCE'), 'bar_type': BarType(BTCUSDT.BINANCE-1-HOUR-LAST-EXTERNAL), 'fast_ema_period': 30, 'slow_ema_period': 100, 'trade_size': Decimal('1')}),
 ImportableStrategyConfig(strategy_path='src.strategies.nautilus:SmaCrossNT', config_path='src.strategies.nautilus:SmaCrossConfig', config={'instrument_id': InstrumentId('BTCUSDT.BINANCE'), 'bar_type': BarType(BTCUSDT.BINANCE-1-HOUR-LAST-EXTERNAL), 'fast_sma_period': 30, 'slow_sma_period': 100, 'trade_size': Decimal('1')})]

Configure Engine:

The BacktestDataConfig objects are integrated into the backtesting framework through BacktestRunConfig:
(https://nautilustrader.io/docs/latest/concepts/data/#integration-with-backtestrunconfig)

In [17]:
run_config = BacktestRunConfig(
    engine=BacktestEngineConfig(strategies=strategies),
    venues=[venue_config],
    data=[data_config],
)
run_config

BacktestRunConfig(venues=[BacktestVenueConfig(name='BINANCE', oms_type='NETTING', account_type='CASH', starting_balances=[Money(1000000.00000000, USDT), Money(1.00000000, BTC)], base_currency=None, default_leverage=1.0, leverages=None, margin_model=None, modules=None, fill_model=None, latency_model=None, fee_model=None, book_type='L1_MBP', routing=False, reject_stop_orders=True, support_gtd_orders=True, support_contingent_orders=True, use_position_ids=True, use_random_ids=False, use_reduce_only=True, bar_execution=True, bar_adaptive_high_low_ordering=False, trade_execution=False, allow_cash_borrowing=False, frozen_account=False)], data=[BacktestDataConfig(catalog_path='/Users/ezequiel.rivero/personal/tradelab_repositories/Crypto-Backtester-Duel/notebooks/catalog', data_cls=<class 'nautilus_trader.model.data.Bar'>, catalog_fs_protocol=None, catalog_fs_storage_options=None, instrument_id=InstrumentId('BTCUSDT.BINANCE'), start_time=None, end_time=None, filter_expr=None, client_id=None, me

In [ ]:
from nautilus_trader.backtest.results import BacktestResult

node = BacktestNode(configs=[run_config])

# Runs one or many configs synchronously
results: list[BacktestResult] = node.run()

2025-10-16T09:53:26.797452000Z [INFO] BACKTESTER-001.BacktestEngine: =================================================================
2025-10-16T09:53:26.797472000Z [INFO] BACKTESTER-001.BacktestEngine:  NAUTILUS TRADER - Automated Algorithmic Trading Platform
2025-10-16T09:53:26.797473000Z [INFO] BACKTESTER-001.BacktestEngine:  by Nautech Systems Pty Ltd.
2025-10-16T09:53:26.797473001Z [INFO] BACKTESTER-001.BacktestEngine:  Copyright (C) 2015-2025. All rights reserved.
2025-10-16T09:53:26.797473002Z [INFO] BACKTESTER-001.BacktestEngine: =================================================================
2025-10-16T09:53:26.797473003Z [INFO] BACKTESTER-001.BacktestEngine: 
2025-10-16T09:53:26.797473004Z [INFO] BACKTESTER-001.BacktestEngine: ⠀⠀⠀⠀⠀⠀⠀⠀⠀⠀⠀⠀⠀⣠⣴⣶⡟⠀⠀⠀⠀⠀⠀⠀⠀⠀⠀⠀⠀⠀⠀
2025-10-16T09:53:26.797473005Z [INFO] BACKTESTER-001.BacktestEngine: ⠀⠀⠀⠀⠀⠀⠀⠀⠀⠀⠀⣰⣾⣿⣿⣿⠀⢸⣿⣿⣿⣿⣶⣶⣤⣀⠀⠀⠀⠀⠀
2025-10-16T09:53:26.797473006Z [INFO] BACKTESTER-001.BacktestEngine: ⠀⠀⠀⠀⠀⠀⢀⣴⡇⢀⣾⣿⣿⣿⣿⣿⠀⣾⣿⣿⣿⣿⣿⣿⣿⠿⠓⠀⠀⠀⠀
2025-10-16T09:53

[INFO] BACKTESTER-001.SmaCrossNT: Bar(BTCUSDT.BINANCE-1-HOUR-LAST-EXTERNAL,62221.99,62371.05,62221.99,62257.73,684.222410,1728223200000000000)
2024-10-06T14:00:00.000000000Z [INFO] BACKTESTER-001.Portfolio: Updated AccountState(account_id=BINANCE-001, account_type=CASH, base_currency=None, is_reported=False, balances=[AccountBalance(total=997_302.77067000 USDT, locked=0.00000000 USDT, free=997_302.77067000 USDT), AccountBalance(total=1.00000000 BTC, locked=0.00000000 BTC, free=1.00000000 BTC)], margins=[], event_id=44d121fd-e321-4f9a-90d3-b38021d574c1)
2024-10-06T14:00:00.000000000Z [INFO] BACKTESTER-001.Portfolio: BTCUSDT.BINANCE net_position=0
2024-10-06T14:00:00.000000000Z [INFO] BACKTESTER-001.EMACross: <--[EVT] OrderFilled(instrument_id=BTCUSDT.BINANCE, client_order_id=O-20241006-140000-001-000-4, venue_order_id=BINANCE-1-006, account_id=BINANCE-001, trade_id=BINANCE-1-292, position_id=BTCUSDT.BINANCE-EMACross-000, order_side=BUY, order_type=MARKET, last_qty=1.000000, last_px=62_2

In [19]:
from nautilus_trader.backtest.engine import BacktestEngine

engine: BacktestEngine = node.get_engine(run_config.id)

account_report = pl.DataFrame(engine.trader.generate_account_report(BINANCE_VENUE))
orders_report = pl.DataFrame(engine.trader.generate_orders_report())
positions_report = pl.DataFrame(engine.trader.generate_positions_report())

In [20]:
account_report.head()

shape: (5, 10)
┌────────────┬───────────┬───────────┬──────────┬───┬───────────┬───────────┬──────────┬───────────┐
│ total      ┆ locked    ┆ free      ┆ currency ┆ … ┆ base_curr ┆ margins   ┆ reported ┆ info      │
│ ---        ┆ ---       ┆ ---       ┆ ---      ┆   ┆ ency      ┆ ---       ┆ ---      ┆ ---       │
│ str        ┆ str       ┆ str       ┆ str      ┆   ┆ ---       ┆ list[null ┆ bool     ┆ struct[0] │
│            ┆           ┆           ┆          ┆   ┆ str       ┆ ]         ┆          ┆           │
╞════════════╪═══════════╪═══════════╪══════════╪═══╪═══════════╪═══════════╪══════════╪═══════════╡
│ 1000000.00 ┆ 0.0000000 ┆ 1000000.0 ┆ USDT     ┆ … ┆ null      ┆ []        ┆ true     ┆ {}        │
│ 000000     ┆ 0         ┆ 0000000   ┆          ┆   ┆           ┆           ┆          ┆           │
│ 1.00000000 ┆ 0.0000000 ┆ 1.0000000 ┆ BTC      ┆ … ┆ null      ┆ []        ┆ true     ┆ {}        │
│            ┆ 0         ┆ 0         ┆          ┆   ┆           ┆           ┆          ┆           │
│ 934210.276 ┆ 0.0000000 ┆ 934210.27 ┆ USDT     ┆ … ┆ null      ┆ []        ┆ false    ┆ {}        │
│ 00000      ┆ 0         ┆ 600000    ┆          ┆   ┆           ┆           ┆          ┆           │
│ 2.00000000 ┆ 0.0000000 ┆ 2.0000000 ┆ BTC      ┆ … ┆ null      ┆ []        ┆ false    ┆ {}        │
│            ┆ 0         ┆ 0         ┆          ┆   ┆           ┆           ┆          ┆           │
│ 868420.552 ┆ 0.0000000 ┆ 868420.55 ┆ USDT     ┆ … ┆ null      ┆ []        ┆ false    ┆ {}        │
│ 00000      ┆ 0         ┆ 200000    ┆          ┆   ┆           ┆           ┆          ┆           │
└────────────┴───────────┴───────────┴──────────┴───┴───────────┴───────────┴──────────┴───────────┘

In [21]:
orders_report.head()

shape: (5, 31)
┌────────────┬────────────┬────────────┬────────────┬───┬──────┬───────────┬───────────┬───────────┐
│ trader_id  ┆ strategy_i ┆ instrument ┆ venue_orde ┆ … ┆ tags ┆ init_id   ┆ ts_init   ┆ ts_last   │
│ ---        ┆ d          ┆ _id        ┆ r_id       ┆   ┆ ---  ┆ ---       ┆ ---       ┆ ---       │
│ str        ┆ ---        ┆ ---        ┆ ---        ┆   ┆ str  ┆ str       ┆ i64       ┆ i64       │
│            ┆ str        ┆ str        ┆ str        ┆   ┆      ┆           ┆           ┆           │
╞════════════╪════════════╪════════════╪════════════╪═══╪══════╪═══════════╪═══════════╪═══════════╡
│ BACKTESTER ┆ EMACross-0 ┆ BTCUSDT.BI ┆ BINANCE-1- ┆ … ┆ null ┆ 958dfc53- ┆ 172755360 ┆ 172755360 │
│ -001       ┆ 00         ┆ NANCE      ┆ 001        ┆   ┆      ┆ 7108-4170 ┆ 000000000 ┆ 000000000 │
│            ┆            ┆            ┆            ┆   ┆      ┆ -b818-e91 ┆ 0         ┆ 0         │
│            ┆            ┆            ┆            ┆   ┆      ┆ b23…      ┆           ┆           │
│ BACKTESTER ┆ SmaCrossNT ┆ BTCUSDT.BI ┆ BINANCE-1- ┆ … ┆ null ┆ 2a3a8016- ┆ 172755360 ┆ 172755360 │
│ -001       ┆ -001       ┆ NANCE      ┆ 002        ┆   ┆      ┆ 9585-479b ┆ 000000000 ┆ 000000000 │
│            ┆            ┆            ┆            ┆   ┆      ┆ -8399-980 ┆ 0         ┆ 0         │
│            ┆            ┆            ┆            ┆   ┆      ┆ faf…      ┆           ┆           │
│ BACKTESTER ┆ SmaCrossNT ┆ BTCUSDT.BI ┆ BINANCE-1- ┆ … ┆ null ┆ 13efe08e- ┆ 172768680 ┆ 172768680 │
│ -001       ┆ -001       ┆ NANCE      ┆ 003        ┆   ┆      ┆ c426-48d5 ┆ 000000000 ┆ 000000000 │
│            ┆            ┆            ┆            ┆   ┆      ┆ -a1b1-72d ┆ 0         ┆ 0         │
│            ┆            ┆            ┆            ┆   ┆      ┆ e31…      ┆           ┆           │
│ BACKTESTER ┆ EMACross-0 ┆ BTCUSDT.BI ┆ BINANCE-1- ┆ … ┆ null ┆ 25328d49- ┆ 172769040 ┆ 172769040 │
│ -001       ┆ 00         ┆ NANCE      ┆ 004        ┆   ┆      ┆ 5af5-4ec8 ┆ 000000000 ┆ 000000000 │
│            ┆            ┆            ┆            ┆   ┆      ┆ -a3e9-a43 ┆ 0         ┆ 0         │
│            ┆            ┆            ┆            ┆   ┆      ┆ 5a6…      ┆           ┆           │
│ BACKTESTER ┆ EMACross-0 ┆ BTCUSDT.BI ┆ BINANCE-1- ┆ … ┆ null ┆ bcf67a4c- ┆ 172769040 ┆ 172769040 │
│ -001       ┆ 00         ┆ NANCE      ┆ 005        ┆   ┆      ┆ 4f26-4116 ┆ 000000000 ┆ 000000000 │
│            ┆            ┆            ┆            ┆   ┆      ┆ -8450-9ac ┆ 0         ┆ 0         │
│            ┆            ┆            ┆            ┆   ┆      ┆ 6dc…      ┆           ┆           │
└────────────┴────────────┴────────────┴────────────┴───┴──────┴───────────┴───────────┴───────────┘

In [22]:
positions_report.head()

shape: (5, 21)
┌───────────┬───────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬──────────┐
│ trader_id ┆ strategy_ ┆ instrumen ┆ account_i ┆ … ┆ commissio ┆ realized_ ┆ realized_ ┆ is_snaps │
│ ---       ┆ id        ┆ t_id      ┆ d         ┆   ┆ ns        ┆ return    ┆ pnl       ┆ hot      │
│ str       ┆ ---       ┆ ---       ┆ ---       ┆   ┆ ---       ┆ ---       ┆ ---       ┆ ---      │
│           ┆ str       ┆ str       ┆ str       ┆   ┆ list[str] ┆ f64       ┆ str       ┆ bool     │
╞═══════════╪═══════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪══════════╡
│ BACKTESTE ┆ SmaCrossN ┆ BTCUSDT.B ┆ BINANCE-0 ┆ … ┆ ["130.035 ┆ -0.02149  ┆ -1542.455 ┆ false    │
│ R-001     ┆ T-001     ┆ INANCE    ┆ 01        ┆   ┆ 58000     ┆           ┆ 58000     ┆          │
│           ┆           ┆           ┆           ┆   ┆ USDT"]    ┆           ┆ USDT      ┆          │
│ BACKTESTE ┆ EMACross- ┆ BTCUSDT.B ┆ BINANCE-0 ┆ … ┆ ["129.265 ┆ -0.03321  ┆ -2312.255 ┆ true     │
│ R-001     ┆ 000       ┆ INANCE    ┆ 01        ┆   ┆ 01000     ┆           ┆ 01000     ┆          │
│           ┆           ┆           ┆           ┆   ┆ USDT"]    ┆           ┆ USDT      ┆          │
│ BACKTESTE ┆ EMACross- ┆ BTCUSDT.B ┆ BINANCE-0 ┆ … ┆ ["125.798 ┆ 0.0202    ┆ 1157.4812 ┆ true     │
│ R-001     ┆ 000       ┆ INANCE    ┆ 01        ┆   ┆ 74000     ┆           ┆ 6000 USDT ┆          │
│           ┆           ┆           ┆           ┆   ┆ USDT"]    ┆           ┆           ┆          │
│ BACKTESTE ┆ EMACross- ┆ BTCUSDT.B ┆ BINANCE-0 ┆ … ┆ ["124.672 ┆ 0.00252   ┆ 32.147720 ┆ true     │
│ R-001     ┆ 000       ┆ INANCE    ┆ 01        ┆   ┆ 28000     ┆           ┆ 00 USDT   ┆          │
│           ┆           ┆           ┆           ┆   ┆ USDT"]    ┆           ┆           ┆          │
│ BACKTESTE ┆ EMACross- ┆ BTCUSDT.B ┆ BINANCE-0 ┆ … ┆ ["125.263 ┆ -0.00695  ┆ -559.1930 ┆ true     │
│ R-001     ┆ 000       ┆ INANCE    ┆ 01        ┆   ┆ 03000     ┆           ┆ 3000 USDT ┆          │
│           ┆           ┆           ┆           ┆   ┆ USDT"]    ┆           ┆           ┆          │
└───────────┴───────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴──────────┘

## Save results

In [23]:
# Create a dictionary of your reports
reports_to_save = {
    "account_report": account_report.drop(["margins", "info"]),
    "orders_report": orders_report.explode("commissions"),
    "positions_report": positions_report.explode("commissions")
}

# Loop through the dictionary's items
for report_name, report_df in reports_to_save.items():
    # Use the string key (report_name) for the filename
    file_path = f"../data/nautilus_bt_{report_name}.csv"
    print(f"Saving {report_name} to {file_path}")
    report_df.sample(10).write_csv(file_path)

Saving account_report to ../data/nautilus_bt_account_report.csv
Saving orders_report to ../data/nautilus_bt_orders_report.csv
Saving positions_report to ../data/nautilus_bt_positions_report.csv


In [25]:
from __future__ import annotations

from dataclasses import asdict, is_dataclass
from typing import Any, Optional

import polars as pl
from nautilus_trader.backtest.results import BacktestResult


class NautilusBackTestAnalyzer:
    """
    Results-only analyzer.
    - Ingests list[BacktestResult].
    - Extracts run metadata, balances, commissions, built-in stats.
    - Produces metrics_wide and metrics_long DataFrames.
    - Prints a compact summary for sections with available data.
    """

    def __init__(self, results: list[BacktestResult]):
        self.results = list(results)
        if not self.results:
            raise ValueError("results must be a non-empty iterable of BacktestResult")
        self._wide: Optional[pl.DataFrame] = None
        self._long: Optional[pl.DataFrame] = None

    # ------------------------
    # Main API
    # ------------------------
    def parse_results(self) -> pl.DataFrame:
        """
        Flatten BacktestResult objects to a normalized table.
        One row per currency at portfolio level.
        Note: strategy-level details depend on your result payload;
        this phase records portfolio aggregates only if that is what results provide.
        """
        rows = []
        for r in self.results:
            # Best-effort accessors. Adjust keys if your BacktestResult differs.
            # Prefer attributes; fall back to dict for dataclasses.
            src = _to_dict_like(r)

            run_id = _get(src, ["run_id", "id", "run", "runId"])
            run_config_id = _get(src, ["run_config_id", "runConfigId"])
            started = _get(src, ["backtest_start", "start", "backtestStart"])
            finished = _get(src, ["backtest_end", "end", "backtestEnd"])
            elapsed = _get(src, ["elapsed", "elapsed_time", "elapsedTime"])
            venue = _get(src, ["venue", "venue_name", "venueName", "venues", "exchange"])
            instrument_ids = _get(src, ["instrument_ids", "instrumentIds", "instruments"])
            totals = _get(src, ["totals", "summary", "stats"], default={})
            # Balances and commissions often live under an account/portfolio block
            acct = _get(src, ["account", "portfolio", "balances"], default={})
            start_balances = _first_non_none(
                _get(acct, ["starting_balances", "start_balances", "startingBalances"]),
                _get(src, ["starting_balances", "start_balances"]),
                [],
            )
            end_balances = _first_non_none(
                _get(acct, ["ending_balances", "end_balances", "endingBalances"]),
                _get(src, ["ending_balances", "end_balances"]),
                [],
            )
            commissions = _first_non_none(
                _get(acct, ["commissions", "fees_total", "commissions_total"]),
                _get(src, ["commissions", "commissions_total", "fees_total"]),
                {},
            )

            # Built-in post-run blocks (names vary). Expect simple numbers.
            builtins = _first_non_none(
                _get(src, ["analysis", "post_run", "postRun", "performance", "returns_stats"]),
                {},
            )

            # Normalize balances to list of dicts: [{"currency": "USDT", "start": 1e6, "end": 9.58e5}, ...]
            start_map = _balances_to_map(start_balances)
            end_map = _balances_to_map(end_balances)
            comm_map = _commissions_to_map(commissions)

            currencies = sorted(set(start_map) | set(end_map) | set(comm_map))
            for cur in currencies:
                start_amt = start_map.get(cur)
                end_amt = end_map.get(cur)
                pnl_total = (None if start_amt is None or end_amt is None else float(end_amt - start_amt))
                pnl_pct_total = (
                    None
                    if start_amt in (None, 0)
                    else float((end_amt / start_amt) - 1.0)
                )

                row = {
                    "run_id": run_id,
                    "run_config_id": run_config_id,
                    "venue": _venue_name(venue),
                    "instrument_ids": str(instrument_ids) if instrument_ids is not None else None,
                    "currency": cur,
                    "backtest_start": started,
                    "backtest_end": finished,
                    "elapsed": str(elapsed) if elapsed is not None else None,
                    "iterations": _get(totals, ["iterations"]),
                    "total_events": _get(totals, ["total_events", "events"]),
                    "total_orders": _get(totals, ["total_orders", "orders"]),
                    "total_positions": _get(totals, ["total_positions", "positions"]),
                    "start_balance": float(start_amt) if start_amt is not None else None,
                    "end_balance": float(end_amt) if end_amt is not None else None,
                    "pnl_total": pnl_total,
                    "pnl_pct_total": pnl_pct_total,
                    # Built-ins if present
                    "returns_vol_annual": _get(builtins, ["returns_volatility", "returns_volatility_annual"]),
                    "avg_return": _get(builtins, ["avg_return", "average_return"]),
                    "avg_win_return": _get(builtins, ["avg_win_return", "average_win_return"]),
                    "avg_loss_return": _get(builtins, ["avg_loss_return", "average_loss_return"]),
                    "sharpe": _get(builtins, ["sharpe", "sharpe_ratio"]),
                    "sortino": _get(builtins, ["sortino", "sortino_ratio"]),
                    "profit_factor": _get(builtins, ["profit_factor"]),
                    "risk_return_ratio": _get(builtins, ["risk_return_ratio"]),
                    "long_ratio": _get(builtins, ["long_ratio"]),
                    "win_rate": _get(builtins, ["win_rate"]),
                    "expectancy_abs": _get(builtins, ["expectancy", "expectancy_abs"]),
                    "best_trade_abs": _get(builtins, ["best_trade", "max_winner"]),
                    "worst_trade_abs": _get(builtins, ["worst_trade", "max_loser"]),
                    "avg_winner_abs": _get(builtins, ["avg_winner"]),
                    "avg_loser_abs": _get(builtins, ["avg_loser"]),
                    "commissions_total": float(comm_map.get(cur)) if comm_map.get(cur) is not None else None,
                }
                rows.append(row)

        df = pl.from_dicts(rows)
        # Minimal dtype hygiene for BQ
        df = df.with_columns(
            pl.col("run_id").cast(pl.Utf8),
            pl.col("run_config_id").cast(pl.Utf8),
            pl.col("venue").cast(pl.Utf8),
            pl.col("instrument_ids").cast(pl.Utf8),
            pl.col("currency").cast(pl.Utf8),
        )
        self._wide = df
        return df

    def run(
        self,
        *,
        rf_rate_annual: float = 0.0,
        periods_per_year: int | None = None,
        print_summary: bool = True,
    ) -> dict[str, pl.DataFrame]:
        """
        Compute immediate metrics from results-only data.
        Returns dict with 'metrics_wide' and 'metrics_long'.
        Sections requiring equity/trades are left null for now.
        """
        if self._wide is None:
            self.parse_results()

        df = self._wide

        # Compute duration in years when start/end are ISO strings if available
        df = df.with_columns(
            _duration_years_expr("backtest_start", "backtest_end").alias("years"),
        ).with_columns(
            pl.when((pl.col("years").is_not_null()) & (pl.col("pnl_pct_total").is_not_null()))
            .then((1.0 + pl.col("pnl_pct_total")) ** (1.0 / pl.col("years")) - 1.0)
            .otherwise(None)
            .alias("cagr")
        )

        # Long view for BQ-friendly metric table
        metrics_cols = [
            "pnl_total",
            "pnl_pct_total",
            "cagr",
            "returns_vol_annual",
            "avg_return",
            "avg_win_return",
            "avg_loss_return",
            "sharpe",
            "sortino",
            "profit_factor",
            "risk_return_ratio",
            "long_ratio",
            "win_rate",
            "expectancy_abs",
            "best_trade_abs",
            "worst_trade_abs",
            "avg_winner_abs",
            "avg_loser_abs",
            "commissions_total",
            "iterations",
            "total_events",
            "total_orders",
            "total_positions",
        ]

        id_cols = [
            "run_id",
            "run_config_id",
            "venue",
            "instrument_ids",
            "currency",
            "backtest_start",
            "backtest_end",
        ]

        long = (
            df.select(id_cols + metrics_cols)
              .unpivot(index=id_cols, on=metrics_cols, variable_name="metric", value_name="value")
        )

        self._wide, self._long = df, long

        if print_summary:
            _print_summary(df)

        return {"metrics_wide": df, "metrics_long": long}


# ------------------------
# Helpers
# ------------------------
def _to_dict_like(obj: Any) -> dict[str, Any]:
    if isinstance(obj, dict):
        return obj
    if is_dataclass(obj):
        return asdict(obj)
    # Fallback: shallow attribute mapping
    d = {}
    for k in dir(obj):
        if k.startswith("_"):
            continue
        try:
            v = getattr(obj, k)
        except Exception:
            continue
        if callable(v):
            continue
        d[k] = v
    return d


def _get(src: Any, keys: list[str], default: Any = None) -> Any:
    """Try multiple key/attr names. Works for dicts of dicts."""
    cur = src
    if cur is None:
        return default
    if isinstance(cur, dict):
        for k in keys:
            if k in cur:
                return cur[k]
        return default
    # Not a dict. Try to access as attributes.
    for k in keys:
        if hasattr(cur, k):
            return getattr(cur, k)
    return default


def _first_non_none(*values):
    for v in values:
        if v is not None:
            return v
    return None


def _balances_to_map(balances: Any) -> dict[str, float]:
    """
    Accepts:
      - list like [Money(100, USD), Money(1, BTC)] serialized or dicts
      - dict like {"USD": 100, "BTC": 1}
    Returns: {"USD": 100.0, "BTC": 1.0}
    """
    if balances is None:
        return {}
    if isinstance(balances, dict):
        return {str(k): float(v) for k, v in balances.items()}
    out: dict[str, float] = {}
    for b in balances if isinstance(balances, (list, tuple)) else [balances]:
        if isinstance(b, dict):
            cur = b.get("currency") or b.get("ccy") or b.get("code")
            amt = b.get("amount") or b.get("value") or b.get("qty") or b.get("quantity")
        else:
            # Fallback for objects with attributes
            cur = getattr(b, "currency", getattr(b, "ccy", getattr(b, "code", None)))
            amt = getattr(b, "amount", getattr(b, "value", getattr(b, "qty", getattr(b, "quantity", None))))
        if cur is None or amt is None:
            continue
        out[str(cur)] = float(amt)
    return out


def _commissions_to_map(commissions: Any) -> dict[str, float]:
    """
    Accepts:
      - scalar numeric (unknown ccy) -> {}
      - dict per currency
      - list of Money-like
    """
    if commissions is None:
        return {}
    if isinstance(commissions, (int, float)):
        return {}
    if isinstance(commissions, dict):
        return {str(k): float(v) for k, v in commissions.items()}
    out: dict[str, float] = {}
    for c in commissions if isinstance(commissions, (list, tuple)) else [commissions]:
        if isinstance(c, dict):
            cur = c.get("currency") or c.get("ccy") or c.get("code")
            amt = c.get("amount") or c.get("value")
        else:
            cur = getattr(c, "currency", getattr(c, "ccy", getattr(c, "code", None)))
            amt = getattr(c, "amount", getattr(c, "value", None))
        if cur is None or amt is None:
            continue
        out[str(cur)] = float(amt)
    return out


def _venue_name(venue_obj: Any) -> Optional[str]:
    if venue_obj is None:
        return None
    if isinstance(venue_obj, str):
        return venue_obj
    # Try to pull name or enum value
    return getattr(venue_obj, "name", getattr(venue_obj, "value", str(venue_obj)))


def _duration_years_expr(start_col: str, end_col: str) -> pl.Expr:
    """
    If ISO8601 timestamps, compute year fraction; else null.
    Uses 365.2425 for civil year.
    """
    return (
        pl.when(pl.col(start_col).is_not_null() & pl.col(end_col).is_not_null())
        .then(
            (
                (pl.col(end_col).str.to_datetime(strict=False) - pl.col(start_col).str.to_datetime(strict=False))
                .dt.total_seconds()
                / (365.2425 * 24 * 3600)
            )
        )
        .otherwise(None)
    )


def _print_summary(df: pl.DataFrame, max_rows: int = 10) -> None:
    """
    Console view for sections 1, 3, 6, 7 using available fields.
    """
    show = df.select(
        "run_id",
        "venue",
        "currency",
        "backtest_start",
        "backtest_end",
        "start_balance",
        "end_balance",
        "pnl_total",
        "pnl_pct_total",
        "cagr",
        "returns_vol_annual",
        "sharpe",
        "sortino",
        "profit_factor",
        "risk_return_ratio",
        "long_ratio",
        "win_rate",
        "expectancy_abs",
        "commissions_total",
        "total_orders",
        "total_positions",
    ).head(max_rows)

    # Minimal deterministic formatting
    def _fmt(x):
        if x is None:
            return "NA"
        if isinstance(x, float):
            return f"{x:.6f}"
        return str(x)

    lines = []
    for row in show.iter_rows(named=True):
        lines.append(
            (
                f"[{row['run_id']}] {row['venue']} {row['currency']}  "
                f"Start: {row['backtest_start']}  End: {row['backtest_end']}\n"
                f"Equity Final: {_fmt(row['end_balance'])}  PnL: {_fmt(row['pnl_total'])}  "
                f"PnL%: {_fmt(row['pnl_pct_total'])}  CAGR: {_fmt(row['cagr'])}\n"
                f"Sharpe: {_fmt(row['sharpe'])}  Sortino: {_fmt(row['sortino'])}  "
                f"Vol(ann): {_fmt(row['returns_vol_annual'])}  PF: {_fmt(row['profit_factor'])}  "
                f"RRR: {_fmt(row['risk_return_ratio'])}  LongRatio: {_fmt(row['long_ratio'])}\n"
                f"WinRate: {_fmt(row['win_rate'])}  Expectancy: {_fmt(row['expectancy_abs'])}  "
                f"Orders: {row['total_orders']}  Positions: {row['total_positions']}  "
                f"Commissions: {_fmt(row['commissions_total'])}"
            )
        )
    print("\n\n".join(lines))


In [28]:
btanalyzer = NautilusBackTestAnalyzer(results)
btanalyzer.parse_results()

NoDataError: no data, cannot infer schema